In [45]:
import folium
from folium import Choropleth, Circle, Marker, Icon, Map
from folium import plugins
from folium.plugins import HeatMap, MarkerCluster
from folium import IFrame
import ipywidgets
#import geopy
#import geocoder

import numpy as np
import pandas as pd

# Mapping and Visualization

## CENTROS MEDICOS EN MADRID

1. COORDENADA-X: coordenada de 6 caracteres sobre plano de la ciudad.

    
2. COORDENADA-Y: coordenada de 7 caracteres sobre plano de la ciudad.

    * Ambas coordenadas, UTM - 30, están proyectadas en el sistema de referencia ETR89. 
    * Actualizado a mayo 2019


3. LATITUD: coordenada latitud en el sistema de referencia WGS84

    
4. LONGITUD: coordenada longitud en el sistema de referencia WGS84

    * La coordenadas longitud y latitud, si se abre el fichero CSV con Excel, las muestra mal por un tema de conversión de EXCEL y manejo de puntos y comas, como separadores. Estos campos, si se abre con otro software, las muestra sin problemas. También está disponible la versión en XML, que los muestra sin problemas ni conversiones. 

In [43]:
centros_medicos_clean = pd.read_csv("../data/centros_medicos_clean.csv")
centros_medicos_clean.head()

Unnamed: 0                                             NOMBRE  \
0           0  Centro Concertado de Atención a las Adicciones...   
1           1  Centro Concertado de Atención a las Adicciones...   
2           2  Centro de Atención a las Adicciones (CAD) de A...   
3           3  Centro de Atención a las Adicciones (CAD) de H...   
4           4  Centro de Atención a las Adicciones (CAD) de L...   

                 DIRECCION    DISTRITO  COD_POSTAL    LATITUD  LONGITUD  \
0  CALLE SANTA HORTENSIA 1   CHAMARTIN       28002  40.446053 -3.670277   
1       AVENIDA PORTUGAL 0      LATINA       28011  40.416331 -3.723991   
2         PASEO CHOPERA 12  ARGANZUELA       28045  40.393057 -3.698067   
3           CALLE MINAYA 7   HORTALEZA       28043  40.468289 -3.636150   
4        CALLE CAMARENA 10      LATINA       28047  40.395971 -3.756272   

                                 TIPO  
0  CentrosAsistenciaDrogodependientes  
1  CentrosAsistenciaDrogodependientes  
2  CentrosAsistenciaDrogodependientes  
3  CentrosAsistenciaDrogodependientes  
4  CentrosAsistenciaDrogodependientes

In [3]:
centros_medicos_clean['TIPO'].unique()

array(['CentrosAsistenciaDrogodependientes', 'OtrosCentrosMedicos',
       'CentrosEspecialidadesMedicas', 'CentrosSalud',
       'CentrosRehabilitacionPsicosocial',
       'CentrosPrevencionEnfermedades', 'CentrosSaludMental',
       'HospitalesClinicasSanatorios'], dtype=object)

In [4]:
max_lat = centros_medicos_clean['LATITUD'].max()
max_lat

40.540270273154896

In [5]:
max_lon = centros_medicos_clean['LONGITUD'].max()
max_lon

-3.57810735476017

### Mapa con markers

In [46]:
map_centros = Map(location=[max_lat, max_lon],zoom_start=10)

In [14]:
for i,row in centros_medicos_clean.iterrows():
    
    tipos = {"location" : [row["LATITUD"], row["LONGITUD"]],
                "tooltip" : row["TIPO"]}
    
    if row["TIPO"] == "CentrosAsistenciaDrogodependientes":
        icon = Icon( color = "white",
                    prefix = "fa",
                    icon = "heartbeat",
                    icon_color = "red"
        )

    elif row["TIPO"] == "OtrosCentrosMedicos":
        icon = Icon( color = "blue",
                    prefix = "fa",
                    icon = "plus-square",
                    icon_color = "white"
        )
     
    elif row["TIPO"] == "CentrosEspecialidadesMedicas":
        icon = Icon( color = "white",
                    prefix = "fa",
                    icon = "medkit",
                    icon_color = "black"
        )
    
    elif row["TIPO"] == "CentrosSalud":
        icon = Icon( color = "white",
                    prefix = "fa",
                    icon = "h-square",
                    icon_color = "blue"
        )
    
    elif row["TIPO"] == "CentrosRehabilitacionPsicosocial":
        icon = Icon( color = "red",
                    prefix = "fa",
                    icon = "heart-o",
                    icon_color = "white"
        )
    
    elif row["TIPO"] == "CentrosPrevencionEnfermedades":
        icon = Icon( color = "white",
                    prefix = "fa",
                    icon = "stethoscope",
                    icon_color = "green"
        )
        
    elif row["TIPO"] == "CentrosSaludMental":
        icon = Icon( color = "white",
                    prefix = "fa",
                    icon = "user-md",
                    icon_color = "black"
        )
    
    # HospitalesClinicasSanatorios
    else:
        icon = Icon(color = "white",
                    prefix = "fa",
                    icon =  "hospital-o",
                    icon_color = "gray"
        )
    
    Marker (**tipos,icon = icon).add_to(map_centros)


map_centros

* CAMBIAR ICONOS POR LOS QUE TIENES GUARDADOS!!

### Mapa de calor

In [37]:
centros_medicos_clean['TIPO'].unique()

array(['CentrosAsistenciaDrogodependientes', 'OtrosCentrosMedicos',
       'CentrosEspecialidadesMedicas', 'CentrosSalud',
       'CentrosRehabilitacionPsicosocial',
       'CentrosPrevencionEnfermedades', 'CentrosSaludMental',
       'HospitalesClinicasSanatorios'], dtype=object)

In [38]:
def dataframescapas(elemento):
    return centros_medicos_clean[centros_medicos_clean['TIPO'].str.contains(f"{elemento}")]

In [39]:
capas = list(centros_medicos_clean['TIPO'].unique())
capas

['CentrosAsistenciaDrogodependientes',
 'OtrosCentrosMedicos',
 'CentrosEspecialidadesMedicas',
 'CentrosSalud',
 'CentrosRehabilitacionPsicosocial',
 'CentrosPrevencionEnfermedades',
 'CentrosSaludMental',
 'HospitalesClinicasSanatorios']

In [40]:
data0 = dataframescapas(capas[0])
data1 = dataframescapas(capas[1])
data2 = dataframescapas(capas[2])
data3 = dataframescapas(capas[3])
data4 = dataframescapas(capas[4])
data5 = dataframescapas(capas[5])
data6 = dataframescapas(capas[6])
data7 = dataframescapas(capas[7])

In [41]:
map_capas = Map(location=[max_lat, max_lon],zoom_start=10)

In [42]:
data0_group = folium.FeatureGroup(name = "Drogodependientes")
HeatMap(data = data0[["LATITUD","LONGITUD"]], radius = 10).add_to(data0_group)
data0_group.add_to(map_capas)


data1_group = folium.FeatureGroup(name = "Otros Centos Medicos")
HeatMap(data = data1[["LATITUD","LONGITUD"]], radius = 10).add_to(data1_group)
data1_group.add_to(map_capas)


data2_group = folium.FeatureGroup(name = "Especialidades Medicas")
HeatMap(data = data2[["LATITUD","LONGITUD"]], radius = 10).add_to(data2_group)
data2_group.add_to(map_capas)

data3_group = folium.FeatureGroup(name = "Centros Salud")
HeatMap(data = data3[["LATITUD","LONGITUD"]], radius = 10).add_to(data3_group)
data3_group.add_to(map_capas)


data4_group = folium.FeatureGroup(name = "Centros Rehabilitacion Psicosocial")
HeatMap(data = data4[["LATITUD","LONGITUD"]], radius = 10).add_to(data4_group)
data4_group.add_to(map_capas)


data5_group = folium.FeatureGroup(name = "Centros Prevencion de Enfermedades")
HeatMap(data = data5[["LATITUD","LONGITUD"]], radius = 10).add_to(data5_group)
data5_group.add_to(map_capas)


data6_group = folium.FeatureGroup(name = "Centros Salud Mental")
HeatMap(data = data6[["LATITUD","LONGITUD"]], radius = 10).add_to(data6_group)
data6_group.add_to(map_capas)


data7_group = folium.FeatureGroup(name = "Hospitales Clinicas Sanatorios")
HeatMap(data = data7[["LATITUD","LONGITUD"]], radius = 10).add_to(data7_group)
data7_group.add_to(map_capas)

# Esta ultima linea SOLO se pone alfinal de haber definido tus capas, para que te aparezca el Later control con todas tus opciones

folium.LayerControl(collapsed = False).add_to(map_capas) 



map_capas

In [ ]:
'''
SALE LA IMAGEN PERO NO EN DONDE TIENE QUE SALIR UBICADA!!

map_icons = Map(location=[max_lat, max_lon],zoom_start=10)

img_incon = folium.raster_layers.ImageOverlay(name = 'icons',
                                            image = '../icons/Hospital-clinica-sanatorio-icon.png',
                                            bounds = [max_lat, max_lon],
                                            opacity = 0.8)

img_incon.add_to(map_icons)

map_icons

'''

## Farmacias en Madrid

In [44]:
farmacias_clean = pd.read_csv("../data/farmacias_clean.csv")
farmacias_clean.head()

Unnamed: 0                titular_nombre                direccion  \
0           0         Amaya Corral Palomino  PLAZA del Dos de Mayo 6   
1           1     Montserrat Gimenez Mestre   CALLE de Ríos Rosas 50   
2           2  Justo Aquilino Corral Aragon    CALLE de Argensola 12   
3           3       Irene Arroita Del Campo       CALLE de Alcalá 98   
4           4          Esther Sansi Ponsico       PLAZA de Salesas 7   

  municipio_nombre    latitud  longitud  
0           Madrid  40.427326 -3.704186  
1           Madrid  40.441590 -3.696234  
2           Madrid  40.425284 -3.694781  
3           Madrid  40.424996 -3.674844  
4           Madrid  40.423736 -3.694447

In [18]:
max_latitud = farmacias_clean.latitud.max()
max_latitud

41.059912104960105

In [19]:
max_longitud = farmacias_clean.longitud.max()
max_longitud

-3.1054510767518786

In [29]:
map_farmacias = Map(location=[max_lat, max_lon],zoom_start=10)
map_farmacias

In [30]:
for i,row in farmacias_clean.iterrows():
    
    tipos = {"location" : [row["latitud"], row["longitud"]],
                "tooltip" : row["titular_nombre"]}
    
    icon = Icon(color = "white",
             prefix = "fa",
             icon = "plus",
             icon_color = "green",
             tooltip =  row["titular_nombre"])
    

    
    Marker (**tipos,icon = icon).add_to(map_farmacias)


map_farmacias

In [31]:
map_farm_calor = Map(location=[max_lat, max_lon],zoom_start=10)

In [32]:
madrid = farmacias_clean[farmacias_clean.municipio_nombre=="Madrid"]
madrid_group = folium.FeatureGroup(name = "Madrid")
HeatMap(data = madrid[["latitud","longitud"]], radius = 15).add_to(madrid_group)
madrid_group.add_to(map_farm_calor)
map_farm_calor

In [35]:
San_Fernando_de_Henares = farmacias_clean[farmacias_clean.municipio_nombre == "San Fernando de Henares"]
San_Fernando_de_Henares_group = folium.FeatureGroup (name = "San Fernando de Henares")
HeatMap(data = San_Fernando_de_Henares[["latitud","longitud"]], radius = 15).add_to(San_Fernando_de_Henares_group)
San_Fernando_de_Henares_group.add_to(map_farm_calor)
folium.LayerControl(collapsed = False).add_to(map_farm_calor)

map_farm_calor

In [33]:
farmacias_clean.municipio_nombre.unique()

array(['Madrid', 'San Fernando de Henares', 'Loeches', 'Getafe',
       'San Sebastián de los Reyes', 'Cercedilla', 'Alcobendas',
       'Guadarrama', 'Morata de Tajuña', 'Carabaña', 'Tielmes',
       'Colmenar Viejo', 'Fuenlabrada', 'Aranjuez',
       'Miraflores de la Sierra', 'Arganda del Rey', 'Cenicientos',
       'Colmenar de Oreja', 'Guadalix de la Sierra', 'Valdemoro',
       'San Lorenzo de El Escorial', 'Moralzarzal', 'Campo Real',
       'Villarejo de Salvanés', 'San Martín de Valdeiglesias',
       'Rivas-Vaciamadrid', 'Alcalá de Henares', 'Rozas de Madrid, Las',
       'Chapinería', 'Buitrago del Lozoya', 'Perales de Tajuña',
       'Torrejón de Ardoz', 'Lozoyuela-Navas-Sieteiglesias',
       'Robledo de Chavela', 'Navalcarnero', 'Molar, El', 'Griñón',
       'Pinto', 'Leganés', 'Ciempozuelos', 'Álamo, El', 'Algete',
       'Valdilecha', 'Móstoles', 'Cadalso de los Vidrios', 'Torrelodones',
       'Collado Villalba', 'Rascafría', 'Villaconejos',
       'San Martín de la Ve